## e621.net/e6ai.net JSON to `.txt` tags
----

This Python script is designed to process JSON files found within a specified directory and its subdirectories. Each JSON file is expected to contain data related to image posts, particularly sourced from online platforms such as image boards. The script parses these JSON files, extracts relevant information such as image URL, ratings, and tags, and generates caption files (`.txt`) based on this data.

Here's a breakdown of what the script does:

1. **Ignoring Tags**: The script defines a list of tags to be ignored during processing, such as "hi res", "shaded", etc.

2. **Processing Files**: The `process_file` function is responsible for processing each JSON file. It reads the JSON data, extracts the URL of the image file, determines its rating, and extracts tags associated with the image.

3. **Generating Caption File**: For each image, a caption file is generated with the same name as the image file but with a .txt extension. The rating of the image is written first, followed by processed tags.

4. **Processing Tags**: Tags are processed to replace underscores with spaces and to handle special cases such as artist tags. Ignored tags are filtered out.

In [1]:
"""
Define tags to be ignored using regular expressions for exact matching
"""
ignored_tags = [r"\bblizzard entertainment\b", r"\bwarcraft\b",
    r"(?:\d{4})|(?:\d+:\d+)",
    r"\bdetailed\b", r"\bwidescreen\b", r"\b4k\b",
    r"\babsurd res\b", r"\bhi res\b", r"\bshaded\b",  r"\bdetailed\b",
    r"\btagme\b",
    r"\bdota\b",
    r"\bcreative commons\b", r"\bcc-by-nc-nd\b",
    r"\bsquare enix\b", r"\bfinal fantasy xiv\b", r"\bfinal fantasy\b",
    r"\bmythological canine\b", r"\basian mythology\b", r"\bmythological scalie\b",
    r"\bancient pokemon\b", r"\bmythological creature\b", r"\blegendary pokemon\b",
    r"\bfelis\b", r"\bfelid\b",
    r"\bsega\b",
    r"\bhasbro\b",
    r"\bzootopia\b",
    r"\bfive nights at freddy's\b",
    r"\beeveelution\b",
    r"\bdisney\b",
    r"\bmammal\b", r"\bcanis\b", r"\bcanine\b", r"\bcanid\b",
    r"\bdigimon\b", r"\bbandai namco\b",
    r"\bpokemon (species)\b",
    r"\bpal (species)\b",
    r"\bpokemon\b", r"\bnintendo\b",
    r"\\bby conditional dnp\\b",
    r"\\bconditional dnp\\b",
    r"\\bconditional_dnp\\b",
    r"\\bby\\s+conditional\\s+dnp\\b",
    r"\bgeneration\s+\d+\s+pokemon\b",
]

In [2]:
import os
import glob
import re
import json
from rich.console import Console
from rich.table import Table

console = Console()


def should_ignore_tag(tag, all_tags):
    for ignored_tag_pattern in ignored_tags:
        pattern = re.compile(ignored_tag_pattern, re.VERBOSE | re.IGNORECASE)
        if any(re.search(pattern, t) for t in all_tags):
            return True
    return False


def process_tags(tags_dict):
    processed_tags = []
    for category, tags_list in tags_dict.items():
        category_tags = []
        if category == "artist":
            category_tags = [
                f"by {tag.replace('_', ' ').replace(' (artist)', '')}"
                for tag in tags_list
                if tag
            ]
        else:
            for tag in tags_list:
                tag = tag.replace("_", " ")
                # Escape unescaped parentheses
                tag = re.sub(r"(?<!\\)\(", r"\(", tag)
                tag = re.sub(r"(?<!\\)\)", r"\)", tag)
                if tag.lower() == "artist":
                    continue
                if not should_ignore_tag(tag):
                    category_tags.append(tag)
        processed_tags.extend(category_tags)
    return processed_tags


def process_file(file_path):
    try:
        console.print(f"Processing file: [bold]{file_path}[/bold]")
        with open(file_path, "r") as f:
            data = json.load(f)
        # Parse the URL and generate filename
        post_data = data.get("post", {})
        file_data = post_data.get("file", {})
        url = file_data.get("url")
        if url:
            filename, ext = os.path.splitext(os.path.basename(url))
            # Create caption file
            caption_file = f"{filename}.txt"
            caption_path = os.path.join(os.path.dirname(file_path), caption_file)
            with open(caption_path, "w", encoding="utf-8") as f:
                # Write rating
                rating = post_data.get("rating", "q")
                if rating == "s":
                    f.write("rating_safe, ")
                elif rating == "e":
                    f.write("rating_explicit, ")
                else:
                    f.write("rating_questionable, ")
                # Process tags
                tags_data = post_data.get("tags", {})
                processed_tags = process_tags(tags_data)
                # Check if there are any valid tags before writing
                if processed_tags:
                    # Join tags with commas and write to file
                    tags_line = ", ".join(processed_tags)
                    f.write(tags_line.strip())

                    # Create a table
                    table = Table(show_header=True, header_style="bold magenta")
                    table.add_column(caption_path, justify="center")

                    table.add_row(tags_line.strip())

                    # Print the table
                    console.print(table)
    except Exception as e:
        console.print(f"Error processing file: [bold]{file_path}[/bold]")
        console.print(e)


def recursive_process(directory):
    for file_path in glob.glob(directory + "/**/*.json", recursive=True):
        process_file(file_path)


if __name__ == "__main__":
    #root_directory = r"E:\training_dir"
    root_directory = r"C:\Users\kade\Desktop\training_dir_staging"
    recursive_process(root_directory)

Processing file: C:\Users\kade\Desktop\training_dir_staging\1_yum\1950095.json

┏━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┓
┃              C:\Users\kade\Desktop\training_dir_staging\1_yum\c0199d005063692aa7c83fee5df1f117.txt              ┃
┡━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┩
│   3 toes, :d, abstract background, amber eyes, animal genitalia, blue body, blue scales, blue wings, border,    │
│ claws, cloaca, countershade arms, countershade face, countershade tail, countershade torso, countershade wings, │
│       countershading, digitigrade, dorsal fin, ear fins, ear frill, feet, female, feral, fin, foot focus,       │
│  foreshortening, frill \(anatomy\), genitals, glistening, glistening body, glistening eyes, glistening scales,  │
│ glistening tail, green body, green scales, green stripes, hindpaw, horizontal cloaca, horn, long neck, looking  │
│       at viewer, looking down, low-angle view, membrane \(anatomy\), membranous wings, multicolored body,       │
│   multicolored scales, nude, open mouth, paws, perspective, pupils, scales, slit pupils, smile, solo, spiked    │
│ tail, spikes, spikes \(anatomy\), spines, spread legs, spreading, striped body, striped scales, stripes, tail,  │
│  tail fin, toes, tongue, tongue out, transparent border, two tone body, two tone scales, two tone wings, white  │
│  body, white countershading, white scales, wing claws, wings, worm's-eye view, by nitrods, european mythology,  │
│   mythology, dardranac, aquatic dragon, dragon, marine, mythological creature, mythological scalie, reptile,    │
│          scalie, western dragon, wyvern, absurd res, alpha channel, digital media \(artwork\), hi res           │
└─────────────────────────────────────────────────────────────────────────────────────────────────────────────────┘

Processing file: C:\Users\kade\Desktop\training_dir_staging\1_yum\2124533.json

┏━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┓
┃              C:\Users\kade\Desktop\training_dir_staging\1_yum\2c20cdbc43e6400446d015ff7145f04f.txt              ┃
┡━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┩
│   :d, anus, athletic, athletic female, athletic humanoid, big breasts, bottomless, breasts, cleavage cutout,    │
│ clitoris, clothed, clothing, cloud, crop top, cutout, feathered wings, feathers, feet, female, foreshortening,  │
│ genitals, hair, legband, light, light body, light skin, looking at viewer, low-angle view, midriff, open mouth, │
│   outside, perspective, plump labia, pussy, reaching towards viewer, shirt, silver hair, smile, solo, spots,    │
│    spread legs, spreading, standing over viewer, sunlight, tail, tail feathers, talons, thick thighs, toes,     │
│   topwear, wings, worm's-eye view, yellow eyes, by nanostar, european mythology, greek mythology, mythology,    │
│   animal humanoid, avian, avian humanoid, harpy, humanoid, mythological avian, mythological creature, winged    │
│                                                humanoid, hi res                                                 │
└─────────────────────────────────────────────────────────────────────────────────────────────────────────────────┘

Processing file: C:\Users\kade\Desktop\training_dir_staging\1_yum\2520326.json

...

┏━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┓
┃              C:\Users\kade\Desktop\training_dir_staging\1_yum\250fadc59841a626a35c73401cb08087.txt              ┃
┡━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┩
│   4 toes, ambiguous gender, anthro, barefoot, biped, black body, black bottomwear, black clothing, black fur,   │
│  black pawpads, black skirt, bottomwear, clipboard, close-up, clothed, clothing, coat, duo, extreme close-up,   │
│  extreme size difference, feet, female, foot focus, foreshortening, fur, grey body, grey fur, hindpaw, holding  │
│    object, inside, lab coat, laboratory, larger anthro, larger female, low-angle view, micro, pawpads, paws,    │
│   perspective, size difference, skirt, smaller ambiguous, soles, solo focus, stepped on, tail, toes, topwear,   │
│                 unaware, walking, worm's-eye view, by jazzumi, holly \(neopuc\), hyena, hi res                  │
└─────────────────────────────────────────────────────────────────────────────────────────────────────────────────┘

Processing file: C:\Users\kade\Desktop\training_dir_staging\1_yum\4668318.json

┏━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┓
┃              C:\Users\kade\Desktop\training_dir_staging\1_yum\de9252d95eee9561328e40d9c37230ee.txt              ┃
┡━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┩
│   4 toes, angry, anthro, anthrofied, arm blush, arm tuft, bangs, barefoot, bent leg, biped, black bottomwear,   │
│  black clothing, black eyebrows, black gloves, black handwear, black nose, black panties, black topwear, black  │
│  underwear, blush, bodily fluids, body blush, bottomwear, breasts, cheek tuft, claws, clothed, clothing, crop   │
│  top, dark eyelids, ear piercing, ear ring, elbow tuft, eyebrows, eyelashes, facial tuft, fangs, feet, female,  │
│       fingerless gloves, foot blush, foot focus, forehead gem, foreshortening, freckles, front view, fur,       │
│    furgonomics, gem, glistening, glistening feet, gloves, hair, handwear, head tuft, humanoid feet, imminent    │
│     stomp, inner ear fluff, looking at viewer, looking down, looking down at viewer, low-angle view, medium     │
│       breasts, midriff, miniskirt, musk, musk clouds, navel, neck tuft, notched ear, open mouth, panties,       │
│   perspective, piercing, plantigrade, pokemorph, raised foot, red eyes, red hair, ring piercing, sharp teeth,   │
│ shirt, simple background, skirt, smelly, smelly feet, soles, solo, standing, steam, steamy feet, sweat, sweaty  │
│  feet, tail, tail through skirt, tail tuft, tail under skirt, teeth, thick eyelashes, toe claws, toes, tongue,  │
│    topwear, torn clothing, torn shirt, torn topwear, tuft, underwear, upskirt, white claws, worm's-eye view,    │
│    wrinkles, by canyams, fan character, fang the weavile, weavile, absurd res, digital drawing \(artwork\),     │
│                                  digital media \(artwork\), hi res, signature                                   │
└─────────────────────────────────────────────────────────────────────────────────────────────────────────────────┘

Processing file: C:\Users\kade\Desktop\training_dir_staging\1_yum\4676120.json

┏━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┓
┃              C:\Users\kade\Desktop\training_dir_staging\1_yum\a52d7eacf5e66d190e1cd967a3800cca.txt              ┃
┡━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┩
│ 3 fingers, 3 toes, >:3, anthro, anthrofied, bangs, barefoot, bedroom eyes, bent legs, biped, black bottomwear,  │
│   black clothing, black eyebrows, black gloves, black handwear, black nose, black topwear, blep, bottomwear,    │
│     breasts, cheek tuft, clawed fingers, claws, closed smile, clothed, clothing, crop top, cute fangs, dark     │
│    eyelids, eyebrow through hair, eyebrows, eyelashes, facial tuft, fangs, feet, female, fingerless gloves,     │
│ fingers, foot focus, forehead gem, foreshortening, freckles, front view, fur, gem, glistening, glistening feet, │
│ gloves, hair, handwear, happy, head tuft, hindpaw, humanoid feet, inner ear fluff, inviting, looking at viewer, │
│     looking down, looking down at viewer, low-angle view, medium breasts, midriff, miniskirt, mouth closed,     │
│ narrowed eyes, naughty face, neck tuft, paws, perspective, plantigrade, pokemorph, presenting, raised hand, red │
│  eyes, red hair, seductive, shirt, simple background, sitting, skirt, smile, smiling at viewer, smirk, snaggle  │
│  tooth, soles, solo, teasing, teeth, text, thick eyelashes, toe claws, toes, tongue, tongue out, topwear, torn  │
│     clothing, torn shirt, torn topwear, translucent, translucent hair, tuft, white claws, worm's-eye view,      │
│ wrinkles, by jammerhighwind, fan character, fang the weavile, weavile, absurd res, digital drawing \(artwork\), │
│                           digital media \(artwork\), hi res, huge filesize, signature                           │
└─────────────────────────────────────────────────────────────────────────────────────────────────────────────────┘

## Delete every JSON file ⚠️

---

In [3]:
import glob
import os

def delete_json_files(directory):
    # Create the path pattern to match JSON files
    pattern = os.path.join(directory, '**', '*.json')
    
    # Find all JSON files using glob
    json_files = glob.glob(pattern, recursive=True)
    
    # Delete each JSON file
    for file_path in json_files:
        try:
            os.remove(file_path)
            print(f"Deleted: {file_path}")
        except OSError as e:
            print(f"Error deleting {file_path}: {e}")

if __name__ == "__main__":
    # Specify the directory path
    #directory_path = r'E:\training_dir'
    directory_path = r'C:\Users\kade\Desktop\training_dir_staging'

    # Call the function to delete JSON files recursively
    delete_json_files(directory_path)

Deleted: C:\Users\kade\Desktop\training_dir_staging\1_yum\1950095.json
Deleted: C:\Users\kade\Desktop\training_dir_staging\1_yum\2124533.json
Deleted: C:\Users\kade\Desktop\training_dir_staging\1_yum\2520326.json
Deleted: C:\Users\kade\Desktop\training_dir_staging\1_yum\3754677.json
Deleted: C:\Users\kade\Desktop\training_dir_staging\1_yum\3768442.json
Deleted: C:\Users\kade\Desktop\training_dir_staging\1_yum\3796853.json
Deleted: C:\Users\kade\Desktop\training_dir_staging\1_yum\3877245.json
Deleted: C:\Users\kade\Desktop\training_dir_staging\1_yum\3931701.json
Deleted: C:\Users\kade\Desktop\training_dir_staging\1_yum\3955194.json
Deleted: C:\Users\kade\Desktop\training_dir_staging\1_yum\4093868.json
Deleted: C:\Users\kade\Desktop\training_dir_staging\1_yum\4124137.json
Deleted: C:\Users\kade\Desktop\training_dir_staging\1_yum\4125643.json
Deleted: C:\Users\kade\Desktop\training_dir_staging\1_yum\4328452.json
Deleted: C:\Users\kade\Desktop\training_dir_staging\1_yum\4480870.json
Delete